###### Webscrape_v7 - borrowed from v6
version 7 being changed to save search information with .cor file.
Currently, searches (such as "inkjet") when successful go to basic pipeline
and get stuff printed out in a separate file. Want that info in the .cor file
so i can use doc2vec on it and use the search results for dot colors.

This may result in substantial changes to the spider - which is currently in good working order
in v6.

https://stackoverflow.com/questions/57616611/python-scrapy-issues-running-imagespipeline-when-running-crawler-from-scrip

In [1]:
import scrapy
import logging
import json
from scrapy.crawler import CrawlerProcess
import pandas as pd
from pandas import read_csv
import csv
from scrapy.shell import inspect_response
import numpy as np
from scrapy.pipelines.images import ImagesPipeline
from scrapy.selector import Selector
import difflib

In [2]:
class JsonWriterPipeline(object):

# in many examples the Pipeline is defined as an object, e.g.
# class JsonWriterPipeline(object):
# strangely this seems to be equivalent to the above, i.e. leaving
# out the "object" argument.
    
    def open_spider(self,spider):
        self.file = open('item.jl', 'w')

    def close_spider(self,spider):
        self.file.close()

    def process_item(self, item,spider):
        print('hello world',dict(item))
        for field in item:
            print ('Json items',field + ': ' + item[field])
            
        line = json.dumps(dict(item)) + "\n"
        self.file.write(line)
        return item

In [3]:
class BasicPipeline(object):
    
    def open_spider(self,spider):
        self.file = open('Ptotal_v2.txt','w')
        
    def close_spider(self,spider):
        self.file.close()
        
    def process_item(self,item,spider):
        line=str(item)
        self.file.write(line + "\n")
        return item

In [4]:
class MyNewPipeline(object):
    
    def open_spider(self,spider):
        self.file = open('items2.jl', 'wb')
        
    def close_spider(self, spider):
        self.file.close()
        
    def process_item(self,item,spider):
        print('processing',dict(item))
        line = json.dumps(dict(item)) + " new " + "\n"
        self.file.write(line)
        return item

In [5]:
class ItemCollectorPipeline(object):
    def __init__(self):
        self.ids_seen = set()
        
    def process_item(self,item,spider):
        print("ItemCollector")
        items.append(item)

In [6]:
class ImageItem(scrapy.Item):
    images = scrapy.Field()
    image_urls = scrapy.Field()

In [7]:
class ItemTest(scrapy.Item):
    Organization = scrapy.Field()
    url = scrapy.Field()
    robot = scrapy.Field()
    machine = scrapy.Field()
    tinyML = scrapy.Field()
    brain = scrapy.Field()
    food = scrapy.Field()
    textout = scrapy.Field()

In [8]:
class Print_Item(scrapy.Item):
    Organization = scrapy.Field()
    url = scrapy.Field()
    ThreeDP = scrapy.Field()
    inkjet = scrapy.Field()
    digitalP = scrapy.Field()
    biomaterials = scrapy.Field()
    food = scrapy.Field()
    ScreenPrinting = scrapy.Field()
    textout = scrapy.Field()
    searchterm = scrapy.Field()
    fulltext = scrapy.Field()

In [9]:
class Scrapy2Item(scrapy.Item):
    title = scrapy.Field()
    image_urls = scrapy.Field()
    sku = scrapy.Field()

class Scrapy2Pipeline(ImagesPipeline):
    def get_media_requests(self, item, info):
        return [scrapy.Request(x, meta={'image_name': item['sku']})
                for x in item.get('image_urls', [])]

    def file_path(self, request, response=None, info=None):
        return '%s.jpg' % request.meta['image_name']

In [10]:
class ImgSpider(scrapy.Spider):
    name = "img_spider"
    start_urls = ["https://www.amazon.ca/s?k=821826022317"]
#    domain = "https://www.amazon.ca/s?k=821826022317"
#    print('domain',domain)
    custom_settings = {
        'LOG_LEVEL': logging.WARNING,
        'ITEM_PIPELINES':{'scrapy.pipelines.images.ImagesPipeline':1,
                         '__main__.ItemCollectorPipeline':100}
#        'DOWNLOAD_TIMEOUT':{1200}
    }
    
#    def start_requests(self):
#        yield scrapy.Request(url=ImgSpider.domain, callback = self.parse)
    
    def parse(self, response):
        image = ImageItem()
        img_urls = []
        items = Scrapy2Item()
        
        titlevar = response.css('span.a-text-normal ::text').extract_first()
        imgvar = [response.css('img ::attr(src)').extract_first()]
        print('titlevar',titlevar)
        
        
        for img in response.css("img::attr(src)").extract():
            print("img",img)
            img_urls.append(img)

        items['title'] = titlevar
        items['image_urls'] = imgvar
        print('items',items)
            
        image["image_urls"] = img_urls
        print("image",image)
        
        yield items

In [11]:
class MySpider(scrapy.Spider):
    name = "startups"
    
# read crunchbase file and pick off websites
#    dataset1=read_csv('C:/Users/MStopa/WebScraping&Crunchbase/WebScraping&Crunchbase/Crunchbase/MarketResearch/MarketResearch1.csv')
    dataset1=read_csv('C:/Users/MStopa/WebScraping&Crunchbase/WebScraping&Crunchbase/Crunchbase/Printing/Printingtot_v4.csv')
#    df=dataset1[['Organization Name','Full Description','Headquarters Location','Website']]
    df=dataset1[['Organization Name','Headquarters Location','Website']]
    dfT=dataset1[['Full Description','Website']]
    dfn=df.to_numpy()
    dfTn=dfT.to_numpy()
    dfnl=dfn.tolist()
    dfTnl=dfTn.tolist()
    print('df.shape',df.shape,dfnl[3][1])
    print('dfT.shape',dfT.shape)
    ii1=-1
    ii2=-1
    ii3=-1
    df2=[]
    dfT2=[]
    for kk in range(dfn.shape[0]): # eliminate nans, specify U.S.
        if str(dfn[kk,2]) != 'nan' and str(dfn[kk,1]) != 'nan': # use numpy for tests
            if 'United States' in dfn[kk,1]:
                ii1+=1
                df2.append(dfnl[kk][:]) # use lists for appending (not easy with numpy)
                dfT2.append(dfTnl[kk][:])
            else:
                ii2+=1
        else:
            ii3+=1


    print('ii1',ii1,'ii2',ii2,'ii3',ii3)
    df2n=np.array(df2) # convert list to numpy - easier to slice
    dfT2n=np.array(dfT2)
    print('df2n.shape',df2n.shape,'dfT2n.shape',dfT2n.shape)
    minc=0
    maxc=df2n.shape[0]
    fulltextCB=dfT2n[minc:maxc,0]
    companies=df2n[minc:maxc,0].tolist() # slice numpy array, change it to a list
    start_urlsB=df2n[minc:maxc,2] # numpy - this is an intermediate step, start_urlsB no longer used
    start_urls=start_urlsB.tolist() # basic starting urls for scrapy - limited to U.S., nans eliminated
    iout1=-1
    iout2=-1

#     start_urlsA=df2n[:,2]
#     start_urlsB=start_urlsA[0:6000]
#     start_urls = start_urlsB.tolist()
#     companies=df['Organization Name'].to_numpy().tolist()
#    print('companies[0]',companies[0])


    custom_settings = {
        'LOG_LEVEL': logging.DEBUG,
        'ITEM_PIPELINES':{'__main__.ItemCollectorPipeline':10},
        'ITEM_PIPELINES':{'scrapy.pipelines.images.ImagesPipeline':100},
        'ITEM_PIPELINES':{'MyNewPipeline':6},
        'ITEM_PIPELINES':{'__main__.JsonWriterPipeline':12},
        'ITEM_PIPELINES':{'__main__.BasicPipeline':4},
    }
    
    count=0
    url_list=[]
    def parse(self, response):
        search1='/technology'
        search2='careers'
        search_list1=['inkjet head','digital printing','ink materials','additive manufacturing',\
                     'direct digital printing','biomaterials','printing for food','screen printing',\
                    'robotic arm','digital manufacturing','inkjet','dimatix']
        search_list2=['webscraping']
        search_list=search_list1
        sitep=response.xpath('//p/text()').getall()
        siteHref=response.xpath('//a/@href').getall()
        badchars = ["\U0001f48c","\U0001f4f1","\u2011","\u301d","\ufb01","\u2023","\u011f","\u1ea3","\U0001f973",\
                    "\U0001f973","\U0001f4da","\U0001f33f","\u2192","\u200d","\u2028","\u24d2","\u2011",\
                   "\u010d","\U0001f64c","\u200b","\ufb02","\ufeff","\u202f","u2070","\u2009",\
                    "\u03bc","\u27a1","\u2033","\U0001f600","\n","\t","\r"]
        bcnum=len(badchars)

        for idx,string1 in enumerate(sitep):
            for jj in range(bcnum):
                string1 = string1.replace(badchars[jj],'')

            string1 = string1.replace(u'xa0',u' ')

            if string1:
                if string1[-1] != '.':
                    string1 += '.'
                    
            sitep[idx]=string1
            
        for idy, string2 in enumerate(siteHref):
            first_hit=False
            if search1 == string2 and not(first_hit): # is 'technology' in any of the scraped links?
                first_hit=True
                technology_page=response.urljoin(string2) # cf https://docs.scrapy.org/en/latest/intro/tutorial.html
                yield scrapy.Request(technology_page, callback=self.parse)
                
                    
        out1=' '.join(sitep)

        site_url=response.url
        site_url_close=difflib.get_close_matches(site_url,self.start_urls,cutoff=0.2) # http -> https e.g.
        print('site_url',site_url,'site_url_close',site_url_close)

        if site_url_close:
            print('site_url_close[0]',site_url_close[0])
            site_urlB=site_url_close[0]
        else:
             site_urlB=site_url

        if site_urlB in self.start_urls:
            ii = self.start_urls.index(site_urlB)
        else:
            ii=-1

        print('ii',ii,'self.companies[ii]',self.companies[ii])
            
        items=Print_Item()
        
        for idz,search_term in enumerate(search_list):
            result1 = [elem for elem in sitep if search_term in elem]
            if result1:
                self.url_list.append(response.url)
                items['searchterm']=search_term
                items['Organization']=self.companies[ii]
                items['fulltext']=self.fulltextCB[ii]
                items['url']=response.url
                print('yielding item',search_term)
                yield items
                
        if out1:
            self.iout1+=1
            print('out1 true iout1',self.iout1,'url',site_url)
            file1=open("Ptotal_v2.cor",'a')
            out1=out1.lstrip(' ')
            if ii != -1: # is there a close match to this url in start_urls?
                out2=site_url + ' ' + self.companies[ii] + ' ' + out1
            else:
                out2=site_url + out1 # the url for this presumably sub-page cannot be identified 

            file1.write(out2 + '\n')
        else:
            self.iout2+=1
            print('out1 false iout2',self.iout2,'url',site_url)

        print('companies[0]',self.companies[self.count],'this url',response.url)
        self.count+=1

#        print('\n ii',ii,'company',self.companies[ii],'url',site_url)
#       print('out1 false iout2',self.iout2,' \n ii',ii,'company',self.companies[ii],'url',site_url)
#         subs='3D Printing'
#         result1 = [i for i in sitep if subs in i]
#         if result1: # boolean - list is not empty
#             self.url_list.append(response.url)
#             items['ThreeDP']=response.xpath('//title/text()').get()
#             items['url']=response.url
#             items['textout']=response.xpath('//p/text()').getall()
#             yield items
#         subs2='inkjet'
#         result1 = [i for i in sitep if subs2 in i]
#         if result1: # boolean - list is not empty
#             self.url_list.append(response.url)
#             items['inkjet']=response.xpath('//title/text()').get()
#             items['url']=response.url
#             items['textout']=response.xpath('//p/text()').getall()
#             yield items
#         subs3='food'
#         result1 = [i for i in sitep if subs3 in i]
#         if result1: # boolean - list is not empty
#             self.url_list.append(response.url)
#             items['food']=response.xpath('//title/text()').get()
#             items['url']=response.url
#             items['textout']=response.xpath('//p/text()').getall()
#             yield items           
#         subs4='digital printing'
#         result1 = [i for i in sitep if subs4 in i]
#         if result1: # boolean - list is not empty
#             self.url_list.append(response.url)
#             items['digitalP']=response.xpath('//title/tex()').get()
#             items['url']=response.url
#             items['textout']=response.xpath('//p/text()').getall()
#             yield items
# print('\n url',subs2,response.url)
#         with open('test1.txt','a') as page:
#             page.write(str(sitep))
#             page.close()
#         if 'https' in site_url:
#             site_urlB = site_url.replace('https','http')
#             print('site_urlB',site_urlB)
#         else:
#             site_urlB = site_url
#             print('site_urlB',site_urlB)

df.shape (14486, 3) Beijing, Beijing, China
dfT.shape (14486, 2)
ii1 4853 ii2 9171 ii3 459
df2n.shape (4854, 3) dfT2n.shape (4854, 2)


In [12]:
outVar='outside_class'
IMAGES_STORE='C://MStopa/WebScraping/images'
items=[]
process = CrawlerProcess({
    'ITEM_PIPELINES':{'MyNewPipeline':2},
#    "FEEDS": {"items.json": {"format": "json"}},
#    "LOG_FILE": 'scrapy_log.txt',
    "DOWNLOAD_DELAY":8,
    "DOWNLOAD_MAXSIZE":0
})


process.crawl(MySpider)
# process.crawl(ImgSpider)
process.start() # the script will block here until the crawling is finished
# print("image",image)
# print(image)
for item in items:
    print('item',item)

2021-10-28 11:46:08 [scrapy.utils.log] INFO: Scrapy 2.2.0 started (bot: scrapybot)
2021-10-28 11:46:08 [scrapy.utils.log] INFO: Versions: lxml 4.5.2.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.6.10 |Anaconda, Inc.| (default, May  7 2020, 19:46:08) [MSC v.1916 64 bit (AMD64)], pyOpenSSL 19.1.0 (OpenSSL 1.1.1l  24 Aug 2021), cryptography 2.9.2, Platform Windows-10-10.0.19041-SP0
2021-10-28 11:46:08 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2021-10-28 11:46:08 [scrapy.crawler] INFO: Overridden settings:
{'DOWNLOAD_DELAY': 8, 'DOWNLOAD_MAXSIZE': 0, 'LOG_LEVEL': 10}
2021-10-28 11:46:08 [scrapy.extensions.telnet] INFO: Telnet Password: 6e2ee7053b4fa4c5
2021-10-28 11:46:08 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.logstats.LogStats']
2021-10-28 11:46:09 [scrapy.middleware] INFO: Enabled downloader 

site_url https://inkbit3d.com/ site_url_close ['https://inkbit3d.com/', 'http://inkbig.com', 'http://inkd.com']
site_url_close[0] https://inkbit3d.com/
ii 2 self.companies[ii] Inkbit
out1 true iout1 0 url https://inkbit3d.com/
companies[0] VitroLabs this url https://inkbit3d.com/


2021-10-28 11:46:10 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://digifabster.com:443/> from <GET http://digifabster.com>
2021-10-28 11:46:10 [scrapy.core.engine] DEBUG: Crawled (404) <GET https://www.digitalalloys.com/> (referer: None)
2021-10-28 11:46:10 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.printforia.com> (referer: None)


site_url http://www.evolveadditive.com/ site_url_close ['http://www.evolveadditive.com/', 'http://www.cosineadditive.com/', 'https://www.lvadhesive.com/']
site_url_close[0] http://www.evolveadditive.com/
ii 3 self.companies[ii] Evolve Additive Solutions
out1 true iout1 1 url http://www.evolveadditive.com/
companies[0] Essentium this url http://www.evolveadditive.com/
site_url https://www.azul3d.com/ site_url_close ['https://www.azul3d.com/', 'https://www.laz3d.com', 'https://www.nwa3d.com/']
site_url_close[0] https://www.azul3d.com/
ii 8 self.companies[ii] Azul 3D
out1 true iout1 2 url https://www.azul3d.com/
companies[0] Inkbit this url https://www.azul3d.com/


2021-10-28 11:46:11 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.essentium.com> (referer: None)
2021-10-28 11:46:11 [scrapy.spidermiddlewares.httperror] INFO: Ignoring response <404 https://www.digitalalloys.com/>: HTTP status code is not handled or not allowed
2021-10-28 11:46:11 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.fortiusmetals.com/> (referer: None)


...

site_url https://www.displaysandgraphicsinc.com/ site_url_close ['http://www.displaysandgraphicsinc.com/', 'https://www.crossmarkgraphicsinc.com/', 'https://www.bindagraphics.com/']
site_url_close[0] http://www.displaysandgraphicsinc.com/
ii 4852 self.companies[ii] Displays and Graphics Inc.
out1 true iout1 3933 url https://www.displaysandgraphicsinc.com/
companies[0] Mansueto Ventures this url https://www.displaysandgraphicsinc.com/


2021-10-28 12:35:33 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.hhglobal.com/uk> from <GET http://www.inwk.com>
2021-10-28 12:35:38 [scrapy.downloadermiddlewares.retry] ERROR: Gave up retrying <GET https://www.teckwin.com> (failed 3 times): [<twisted.python.failure.Failure twisted.internet.error.ConnectionLost: Connection to the other side was lost in a non-clean fashion: Connection lost.>]
2021-10-28 12:35:38 [scrapy.core.scraper] ERROR: Error downloading <GET https://www.teckwin.com>
Traceback (most recent call last):
  File "C:\Users\MStopa\AppData\Local\Continuum\anaconda3\envs\webscrape\lib\site-packages\scrapy\core\downloader\middleware.py", line 44, in process_request
    return (yield download_func(request=request, spider=spider))
twisted.web._newclient.ResponseNeverReceived: [<twisted.python.failure.Failure twisted.internet.error.ConnectionLost: Connection to the other side was lost in a non-clean fashion: Connection lost.>]
2021-10-28 

site_url https://www.hhglobal.com/uk site_url_close ['https://www.ppi-global.com/', 'https://www.honblue.com/', 'https://www.grlabel.com/']
site_url_close[0] https://www.ppi-global.com/
ii 2121 self.companies[ii] PPI - Precision Pulley & Idler
out1 true iout1 3934 url https://www.hhglobal.com/uk
companies[0] ACH Foam Technologies Inc. this url https://www.hhglobal.com/uk


2021-10-28 12:35:52 [scrapy.downloadermiddlewares.retry] DEBUG: Retrying <GET http://www.impressiveprintpro.com/> (failed 2 times): User timeout caused connection failure: Getting http://www.impressiveprintpro.com/ took longer than 180.0 seconds..
2021-10-28 12:36:03 [scrapy.downloadermiddlewares.retry] DEBUG: Retrying <GET http://www.cdicfl.com/> (failed 2 times): TCP connection timed out: 10060: A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond..
2021-10-28 12:36:09 [scrapy.extensions.logstats] INFO: Crawled 4610 pages (at 36 pages/min), scraped 367 items (at 2 items/min)
2021-10-28 12:36:24 [scrapy.downloadermiddlewares.retry] ERROR: Gave up retrying <GET http://www.cdicfl.com/> (failed 3 times): TCP connection timed out: 10060: A connection attempt failed because the connected party did not properly respond after a period of time, or established conne

2021-10-28 12:41:16 [scrapy.core.engine] INFO: Spider closed (finished)
